In [4]:
import json
# Load JSON data from a file
with open('ayahs.json', 'r', encoding='utf-8') as file:
    data = json.load(file)
data

[{'surah_number': 1,
  'verse_number': 1,
  'content': 'بِسۡمِ ٱللَّهِ ٱلرَّحۡمَٰنِ ٱلرَّحِيمِ',
  'aya_text_emlaey': 'بسم الله الرحمن الرحيم',
  'words': ['بِسۡمِ', 'ٱللَّهِ', 'ٱلرَّحۡمَٰنِ', 'ٱلرَّحِيمِ']},
 {'surah_number': 1,
  'verse_number': 2,
  'content': 'ٱلۡحَمۡدُ لِلَّهِ رَبِّ ٱلۡعَٰلَمِينَ',
  'aya_text_emlaey': 'الحمد لله رب العالمين',
  'words': ['ٱلۡحَمۡدُ', 'لِلَّهِ', 'رَبِّ', 'ٱلۡعَٰلَمِينَ']},
 {'surah_number': 1,
  'verse_number': 3,
  'content': 'ٱلرَّحۡمَٰنِ ٱلرَّحِيمِ',
  'aya_text_emlaey': 'الرحمن الرحيم',
  'words': ['ٱلرَّحۡمَٰنِ', 'ٱلرَّحِيمِ']},
 {'surah_number': 1,
  'verse_number': 4,
  'content': 'مَٰلِكِ يَوۡمِ ٱلدِّينِ',
  'aya_text_emlaey': 'مالك يوم الدين',
  'words': ['مَٰلِكِ', 'يَوۡمِ', 'ٱلدِّينِ']},
 {'surah_number': 1,
  'verse_number': 5,
  'content': 'إِيَّاكَ نَعۡبُدُ وَإِيَّاكَ نَسۡتَعِينُ',
  'aya_text_emlaey': 'إياك نعبد وإياك نستعين',
  'words': ['إِيَّاكَ', 'نَعۡبُدُ', 'وَإِيَّاكَ', 'نَسۡتَعِينُ']},
 {'surah_number': 1,
  'verse_number': 6

In [5]:
from pydub import AudioSegment
import os

def convert_mp3_to_wav(mp3_folder, wav_folder):
    # List all MP3 files in the input folder
    for file_name in os.listdir(mp3_folder):

        if file_name.endswith('.mp3'):
            mp3_path = os.path.join(mp3_folder, file_name)
            wav_file_name = file_name.replace('.mp3', '.wav')
            wav_path = os.path.join(wav_folder, wav_file_name)
            if os.path.exists(wav_path):
                print(f'{wav_path} already exists')
                continue
            else:
                print(f'Converting {mp3_path} to {wav_path}')
            try:
                # Load MP3 and export as WAV
                audio = AudioSegment.from_mp3(mp3_path)
                audio.export(wav_path, format='wav')
                # print(f'Converted {mp3_path} to {wav_path}')
            except Exception as e:
                print(f'Failed to convert {mp3_path} to WAV: {e}')


In [6]:
# Load timings JSON data (update this with the actual path or code to get the timings data)
with open('timings.json', 'r', encoding='utf-8') as timingsfile:
    timings = json.load(timingsfile)

words = []
for item in data:
  for wordIndex, word in enumerate(item.get('words')):
      last = True
      if wordIndex < len(item.get('words'))-1:
          last = False
      words.append({
          "word_number": wordIndex + 1,
          "word": word,
          "last": last,
          "surah_number": item.get('surah_number'),
          "verse_number": item.get('verse_number'),
      })

print(words)
# Loop through your surah files

def segmented_ayah_audio_to_word(input_dir,surah, reciter,jsontimings):
    output_dir = f'word_by_word/{reciter}/{surah}'
    for ayah_index, ayah_path in enumerate(os.listdir(input_dir)):
        
        # Create the output directory if it doesn't exist
        if not os.path.exists(output_dir):
            os.makedirs(output_dir)
        # 114  30 juz 60 hizb 240 rb3 6263 ayha 77429 word
        # Iterate over each item in your JSON data
        for index, (item, time) in enumerate(zip(words, timings)):
            try:
                surah_number = item.get('surah_number')
                ayah_number = item.get('verse_number')
                word = item.get('word')
                last = item.get('last')
                timing = float(time.get(jsontimings))   # Changed 'ID' to 'alafasy_timing' following the Timings JSON reciter_name
                word_number = item.get('word_number')
                if ayah_number == ayah_index+1:
                    print(f"Item: {word}, Time: {timing}")
                if surah_number == 2:
                    break
                
                file_name = os.path.basename(ayah_path)
                print(file_name)
                if file_name != f'{surah_number:03}{ayah_number:03}.wav':
                    continue
                # # Load the audio file
                print(f"Processing {input_dir}/{ayah_path}".replace('\\', '/'))
                audio = AudioSegment.from_file(f'{input_dir}/{ayah_path}'.replace('\\', '/'))
                            
                if not surah_number or not ayah_number or timing is None:
                    print(f"Skipping item due to missing data: {item}, {time}")
                    continue

                # Create directories for and ayah
                ayah_dir = f"{output_dir}/ayah_{ayah_number}"

                os.makedirs(ayah_dir, exist_ok=True)

                # Calculate start and end times in milliseconds
                start_time = timing * 1000  # convert to milliseconds
                next_timing = float(timings[index + 1].get('alafasy_timing', timing + 0.1))
                if last:
                   # Extract segm-ent
                    segment = audio[start_time:]
                else:
                    end_time = start_time + ((next_timing ) - timing) * 1000
                    # Extract segm-ent
                    segment = audio[start_time:end_time]
                    
                # Export segment
                # word_filename = f"word_{item.get('word_number', f'{index +1}')}.wav"  # Changed 'ID' to 'word_number'
                segment.export(os.path.join(ayah_dir, f"{word_number}.wav"), format="wav")

                print(f"Exported {word_number} to {ayah_dir} from {start_time}ms to {end_time}ms")

            except Exception as e:
                print(f"An error occurred: {e}")

[{'word_number': 1, 'word': 'بِسۡمِ', 'last': False, 'surah_number': 1, 'verse_number': 1}, {'word_number': 2, 'word': 'ٱللَّهِ', 'last': False, 'surah_number': 1, 'verse_number': 1}, {'word_number': 3, 'word': 'ٱلرَّحۡمَٰنِ', 'last': False, 'surah_number': 1, 'verse_number': 1}, {'word_number': 4, 'word': 'ٱلرَّحِيمِ', 'last': True, 'surah_number': 1, 'verse_number': 1}, {'word_number': 1, 'word': 'ٱلۡحَمۡدُ', 'last': False, 'surah_number': 1, 'verse_number': 2}, {'word_number': 2, 'word': 'لِلَّهِ', 'last': False, 'surah_number': 1, 'verse_number': 2}, {'word_number': 3, 'word': 'رَبِّ', 'last': False, 'surah_number': 1, 'verse_number': 2}, {'word_number': 4, 'word': 'ٱلۡعَٰلَمِينَ', 'last': True, 'surah_number': 1, 'verse_number': 2}, {'word_number': 1, 'word': 'ٱلرَّحۡمَٰنِ', 'last': False, 'surah_number': 1, 'verse_number': 3}, {'word_number': 2, 'word': 'ٱلرَّحِيمِ', 'last': True, 'surah_number': 1, 'verse_number': 3}, {'word_number': 1, 'word': 'مَٰلِكِ', 'last': False, 'surah_n

In [12]:
def prepare_segmented_audio_files(segment : bool = False):
    base_folder = 'downloaded_audio_files'
    wav_audio_folder = 'wav_audio_files'
    listTimingsKeys = ["alafasy_timing","husary_timing"] # add more reciters timings here from timtings.json follwoing the reciter_name in folder in order
    if not os.path.exists(wav_audio_folder):
        os.makedirs(wav_audio_folder)

    for index,reciter in enumerate(os.listdir(base_folder)):
        segmented_reciter_folder = os.path.join(wav_audio_folder, reciter)
        if not os.path.exists(segmented_reciter_folder):
            os.makedirs(segmented_reciter_folder)
        
        
        for surah in os.listdir(os.path.join(base_folder, reciter)):
            base_surah_folder = os.path.join(base_folder, reciter, surah)
            segmented_surah_folder = os.path.join(wav_audio_folder, reciter, surah)
            if not os.path.exists(segmented_surah_folder):
                os.makedirs(segmented_surah_folder)
            # convet mp3 to wav 
            convert_mp3_to_wav(base_surah_folder, segmented_surah_folder)
            if segment:
                segmented_ayah_audio_to_word(segmented_surah_folder, surah, reciter, listTimingsKeys[index])

prepare_segmented_audio_files()


wav_audio_files\alafasy\surah_1\001001.wav already exists
wav_audio_files\alafasy\surah_1\001002.wav already exists
wav_audio_files\alafasy\surah_1\001003.wav already exists
wav_audio_files\alafasy\surah_1\001004.wav already exists
wav_audio_files\alafasy\surah_1\001005.wav already exists
wav_audio_files\alafasy\surah_1\001006.wav already exists
wav_audio_files\alafasy\surah_1\001007.wav already exists
wav_audio_files\husary\surah_1\001001.wav already exists
wav_audio_files\husary\surah_1\001002.wav already exists
wav_audio_files\husary\surah_1\001003.wav already exists
wav_audio_files\husary\surah_1\001004.wav already exists
wav_audio_files\husary\surah_1\001005.wav already exists
wav_audio_files\husary\surah_1\001006.wav already exists
wav_audio_files\husary\surah_1\001007.wav already exists
wav_audio_files\husary\surah_10\010001.wav already exists
wav_audio_files\husary\surah_10\010002.wav already exists
wav_audio_files\husary\surah_10\010003.wav already exists
wav_audio_files\husar

In [8]:
reciter_names = []
for reciter in os.listdir("word_by_word"):
    if reciter == 'tajweed':
        continue
    reciter_names.append(reciter)
print(reciter_names)

['alafasy', 'husary']


In [9]:
# Loop through your surah files
for item in data:
    # Define paths
    if item.get("surah_number") == 2:
        break
    input_ayah_audios_path = f"word_by_word/{reciter_names[0]}/surah_{item.get("surah_number")}/ayah_{item.get("verse_number")}"
    print(f"ayah audio: ayah_{item.get("verse_number")}")
    # Iterate over each file in the directory
    filenames = sorted(os.listdir(input_ayah_audios_path))
    audioList = []
    for wordindex,filename  in enumerate(filenames):
      words =item.get("words")
      file_path = f"{input_ayah_audios_path}/{filename}"
      if os.path.isfile(file_path):
          # Process the file
          print(f"Processing file: {file_path} {words[wordindex]}")
          audioList.append({
              "word_number": wordindex + 1,
              "word": words[wordindex],
              "audio_path": file_path,
          })
    item["words_audios"] = audioList
# Save the updated JSON data to a file (optional)
with open(f'{reciter_names[0]}_data.json', 'w', encoding='utf-8') as f:
    json.dump(data, f, ensure_ascii=False, indent=4)

# Print the updated data to verify
# print(json.dumps(data, ensure_ascii=False, indent=4))

ayah audio: ayah_1
Processing file: word_by_word/alafasy/surah_1/ayah_1/1.wav بِسۡمِ
Processing file: word_by_word/alafasy/surah_1/ayah_1/2.wav ٱللَّهِ
Processing file: word_by_word/alafasy/surah_1/ayah_1/3.wav ٱلرَّحۡمَٰنِ
Processing file: word_by_word/alafasy/surah_1/ayah_1/4.wav ٱلرَّحِيمِ
ayah audio: ayah_2
Processing file: word_by_word/alafasy/surah_1/ayah_2/1.wav ٱلۡحَمۡدُ
Processing file: word_by_word/alafasy/surah_1/ayah_2/2.wav لِلَّهِ
Processing file: word_by_word/alafasy/surah_1/ayah_2/3.wav رَبِّ
Processing file: word_by_word/alafasy/surah_1/ayah_2/4.wav ٱلۡعَٰلَمِينَ
ayah audio: ayah_3
Processing file: word_by_word/alafasy/surah_1/ayah_3/1.wav ٱلرَّحۡمَٰنِ
Processing file: word_by_word/alafasy/surah_1/ayah_3/2.wav ٱلرَّحِيمِ
ayah audio: ayah_4
Processing file: word_by_word/alafasy/surah_1/ayah_4/1.wav مَٰلِكِ
Processing file: word_by_word/alafasy/surah_1/ayah_4/2.wav يَوۡمِ
Processing file: word_by_word/alafasy/surah_1/ayah_4/3.wav ٱلدِّينِ
ayah audio: ayah_5
Processing fi

In [10]:
import os
import json

# Define the new directory path
reciter_names = "tajweed"
base_directory = "word_to_word/tajweed"

# Loop through your surah files
for item in data:
    # Define paths
    if item.get("surah_number") == 2:
        break
    surah_number = str(item.get("surah_number")).zfill(3)
    ayah_number = str(item.get("verse_number")).zfill(3)
    input_ayah_audios_path = f"word_by_word/tajweed/surah_1"
    print(f"ayah audio: {ayah_number}")
    
    # Iterate over each file in the directory
    filenames = sorted(os.listdir(input_ayah_audios_path))
    words = item.get("words")
    audioList = []
    paths = []
    for filename in filenames:
        # Ensure the filename has the correct format and ends with .mp3
        if (filename.startswith(f"{surah_number}{ayah_number}")) and (filename.endswith(".mp3")):
        # Extract word number from filename by removing the .mp3 extension
            file_path = f"{input_ayah_audios_path}/{filename}"
            paths.append(file_path)
            
    for path in range(len(paths)):
        print(paths[path])
                    # Process the file
        print(f"Processing file: {file_path} {words[path]}")
        audioList.append({
            "word_number": path+1,
            "word": words[path],
            "audio_path": paths[path],
        })
    item["words_audios"] = audioList
        
# Save the updated JSON data to a file (optional)
with open(f'{reciter_names}_data.json', 'w', encoding='utf-8') as f:
    json.dump(data, f, ensure_ascii=False, indent=4)

# Print the updated data to verify
# print(json.dumps(data, ensure_ascii=False, indent=4))


ayah audio: 001
word_by_word/tajweed/surah_1/001001001.mp3
Processing file: word_by_word/tajweed/surah_1/001001004.mp3 بِسۡمِ
word_by_word/tajweed/surah_1/001001002.mp3
Processing file: word_by_word/tajweed/surah_1/001001004.mp3 ٱللَّهِ
word_by_word/tajweed/surah_1/001001003.mp3
Processing file: word_by_word/tajweed/surah_1/001001004.mp3 ٱلرَّحۡمَٰنِ
word_by_word/tajweed/surah_1/001001004.mp3
Processing file: word_by_word/tajweed/surah_1/001001004.mp3 ٱلرَّحِيمِ
ayah audio: 002
word_by_word/tajweed/surah_1/001002001.mp3
Processing file: word_by_word/tajweed/surah_1/001002004.mp3 ٱلۡحَمۡدُ
word_by_word/tajweed/surah_1/001002002.mp3
Processing file: word_by_word/tajweed/surah_1/001002004.mp3 لِلَّهِ
word_by_word/tajweed/surah_1/001002003.mp3
Processing file: word_by_word/tajweed/surah_1/001002004.mp3 رَبِّ
word_by_word/tajweed/surah_1/001002004.mp3
Processing file: word_by_word/tajweed/surah_1/001002004.mp3 ٱلۡعَٰلَمِينَ
ayah audio: 003
word_by_word/tajweed/surah_1/001003001.mp3
Processi